In [1]:
!pip install confluent_kafka

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 37.2 MB/s eta 0:00:0000:0100:01


In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All"
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/dataset3/demo_data.csv


In [3]:
import json
import os
import pandas as pd
from confluent_kafka import Producer

In [4]:
df = pd.read_csv('/kaggle/input/dataset3/demo_data.csv')
df.head(5)

transaction_id  client_id  amount   mcc  credit_limit  card_brand  \
0         7479444        126    0.19  4722         13555  Mastercard   
1         7486725        126  339.00  3640         13555  Mastercard   
2         7490901        720    4.45  4214           974  Mastercard   
3         7490914        720    7.19  5311           974  Mastercard   
4         7491008       1644    8.76  5712         10900        Visa   

  card_type  gender retirement_status  current_age  per_capita_income  \
0     Debit    Male       Not Retired           63              13047   
1     Debit    Male       Not Retired           63              13047   
2     Debit  Female       Not Retired           36               9710   
3     Debit  Female       Not Retired           36               9710   
4    Credit    Male           Retired           83              15406   

   yearly_income  total_debt  Debt_to_Income_Ratio  credit_score  
0          26600           0              0.000000           799  
1          26600           0              0.000000           799  
2          19800       40038              2.022121           682  
3          19800       40038              2.022121           682  
4          31943        1248              0.039070           686

In [5]:
import json
import os
import pandas as pd
from confluent_kafka import Producer

# Setup Kafka producer config
conf = {
    "bootstrap.servers": "pkc-312o0.ap-southeast-1.aws.confluent.cloud:9092",
    "security.protocol": "SASL_SSL",
    "sasl.mechanisms": "PLAIN",
    "sasl.username": "BECRWYYPQA4FNGPW",
    "sasl.password": "FFQ544dYKqJZqMklOrd4V8ApHKLTQhCxm3522zoegl9ngAF3IubQpJ0rlj15D2zF",
    "client.id": "csv-serial-producer"
}

producer = Producer(conf)
topic = "fraud_1"

# Delivery report callback
def delivery_report(err, msg):
    if err:
        print(f"Message delivery failed: {err}")
    else:
        print(f"Message delivered successfully! Key: {msg.key().decode()}")

# Checkpoint functions
def read_checkpoint(checkpoint_file):
    if os.path.exists(checkpoint_file):
        with open(checkpoint_file, 'r') as file:
            return int(file.read().strip())
    return 0

def write_checkpoint(checkpoint_file, index):
    with open(checkpoint_file, 'w') as file:
        file.write(str(index))
    print(f"Checkpoint updated to line: {index}")

# Handle non-serializable objects
def handle_date(obj):
    if isinstance(obj, pd.Timestamp):
        return obj.strftime('%Y-%m-%d %H:%M:%S')
    raise TypeError(f"Object of type {type(obj).__name__} is not JSON serializable")

# Stream CSV to Kafka
def stream_csv_serially(file_path, key_column=None, checkpoint_file='/kaggle/working/checkpoint.txt', batch_size=100):
    df = pd.read_csv(file_path)
    last_sent_index = read_checkpoint(checkpoint_file)

    for idx, row in df.iterrows():
        if idx < last_sent_index:
            continue

        try:
            record = row.to_dict()
            record_json = json.dumps(record, default=handle_date)

            key = str(record[key_column]) if key_column and key_column in record else str(idx)

            producer.produce(
                topic=topic,
                key=key.encode('utf-8'),
                value=record_json.encode('utf-8'),
                callback=delivery_report
            )

            if (idx + 1) % batch_size == 0:
                producer.flush()
                write_checkpoint(checkpoint_file, idx + 1)

        except Exception as e:
            print(f"Error processing row {idx}: {e}")

    # Flush và checkpoint sau cùng
    producer.flush()
    write_checkpoint(checkpoint_file, len(df))

# Main
if __name__ == "__main__":
    stream_csv_serially('/kaggle/input/dataset3/demo_data.csv', key_column="transaction_id")


Message delivered successfully! Key: 7502435
Message delivered successfully! Key: 7506395
Message delivered successfully! Key: 7513807
Message delivered successfully! Key: 7513871
Message delivered successfully! Key: 7514305
Message delivered successfully! Key: 7541474
Message delivered successfully! Key: 7544897
Message delivered successfully! Key: 7545630
Message delivered successfully! Key: 7545651
Message delivered successfully! Key: 7560321
Message delivered successfully! Key: 7560537
Message delivered successfully! Key: 7568636
Message delivered successfully! Key: 7574474
Message delivered successfully! Key: 7576839
Message delivered successfully! Key: 7581541
Message delivered successfully! Key: 7582129
Message delivered successfully! Key: 7582407
Message delivered successfully! Key: 7592537
Message delivered successfully! Key: 7592955
Message delivered successfully! Key: 7506125
Message delivered successfully! Key: 7541336
Message delivered successfully! Key: 7541624
Message de

%6|1752575638.227|GETSUBSCRIPTIONS|csv-serial-producer#producer-1| [thrd:main]: Telemetry client instance id changed from AAAAAAAAAAAAAAAAAAAAAA to H/XRfMfdRNi3HdJin6Ushg


Message delivered successfully! Key: 7596796
Message delivered successfully! Key: 7596878
Message delivered successfully! Key: 7597372
Message delivered successfully! Key: 7597985
Message delivered successfully! Key: 7598351
Message delivered successfully! Key: 7600677
Message delivered successfully! Key: 7601108
Message delivered successfully! Key: 7608555
Message delivered successfully! Key: 7609332
Message delivered successfully! Key: 7609398
Message delivered successfully! Key: 7612703
Message delivered successfully! Key: 7613455
Message delivered successfully! Key: 7622722
Message delivered successfully! Key: 7593639
Message delivered successfully! Key: 7594592
Message delivered successfully! Key: 7600496
Message delivered successfully! Key: 7601780
Message delivered successfully! Key: 7602194
Message delivered successfully! Key: 7604899
Message delivered successfully! Key: 7605268
Message delivered successfully! Key: 7610269
Message delivered successfully! Key: 7610732
Message de